In [1]:
# Ensure project root (OpenCEP) is on sys.path for imports like `from base.Pattern import Pattern`
import sys, os, pathlib

nb_dir = (
    pathlib.Path(__file__).parent if "__file__" in globals() else pathlib.Path.cwd()
)
project_root = str((nb_dir / "..").resolve())
if project_root not in sys.path:
    sys.path.insert(0, project_root)

from datetime import timedelta
from CEP import CEP
from base.Pattern import Pattern
from base.PatternStructure import (
    SeqOperator,
    PrimitiveEventStructure,
    KleeneClosureOperator,
)
from condition.CompositeCondition import AndCondition
from condition.Condition import Variable, SimpleCondition
from condition.KCCondition import KCIndexCondition
from stream.FileStream import FileOutputStream
from stream.DataFrameStream import CitiBikeDataFrameInputStream
from plugin.citibike.CitiBike2 import (
    CitiBikeTripEventTypeClassifier,
    CitiBikeDataFormatter,
)
import test
from tree.PatternMatchStorage import TreeStorageParameters
from parallel.ParallelExecutionParameters import (
    DataParallelExecutionParametersHirzelAlgorithm,
)
from parallel.ParallelExecutionPlatforms import ParallelExecutionPlatforms
from plugin.citibike.RessourceConsumption import RessourceConsumption

monitor = RessourceConsumption()


In [2]:
def get_pattern(timedelta_minutes=31):
    citibikeHotPathsPattern = Pattern(
        SeqOperator(
            KleeneClosureOperator(PrimitiveEventStructure("CitiBikeTrip", "a"), max_size=5),
            PrimitiveEventStructure("CitiBikeTrip", "b"),
        ),
        AndCondition(
            KCIndexCondition(
                names={"a"},
                getattr_func=lambda x: x["bikeid"],
                relation_op=lambda a1, a2: a1 == a2,
                offset=-1,
            ),
            KCIndexCondition(
                names={"a"},
                getattr_func=lambda x: (
                    int(float(x["startstationid"])),
                    int(float(x["endstationid"])),
                ),
                relation_op=lambda a1, a2: a1[0] == a2[1],
                offset=-1,
            ),
            SimpleCondition(
                Variable("a", lambda x: x[-1]["bikeid"]),
                Variable("b", lambda x: x["bikeid"]),
                relation_op=lambda a, b: a == b,
            ),
            SimpleCondition(
                Variable("a", lambda x: int(float(x[-1]["endstationid"]))),
                Variable("b", lambda x: int(float(x["startstationid"]))),
                relation_op=lambda a, b: a == b,
            ),
            SimpleCondition(
                Variable("b", lambda x: int(float(x["endstationid"]))),
                relation_op=lambda end_id: str(end_id) in {"111111"},
            ),
        ),
        timedelta(minutes=timedelta_minutes),
    )
    return citibikeHotPathsPattern

# VARIANT 1
#### RECENT_LATENCIES_INTERVAL = 1000

In [3]:
# VARIANT 1
input_file = "../test/EventFiles/201901-citibike-tripdata-1-fabricated-original.csv"
output_file = "output_citibike_VARIANT_1.txt"

citibikeHotPathsPattern = get_pattern(timedelta_minutes=31)
load_shedding_threshold = 30  # when to start load shedding - length of partial match array
load_shedding_drop_rate = 0.3  # how many matches to drop when load shedding is active
latency_bound = 0.08  # in seconds


load_shedding_params = TreeStorageParameters(
    sort_storage=True,
    enable_load_shedding=True,
    load_shedding_threshold=load_shedding_threshold,
    load_shedding_drop_rate=load_shedding_drop_rate,
    load_shedding_strategy="oldest",
    clean_up_interval=10,
    latency_bound=latency_bound,
)
dp_params = DataParallelExecutionParametersHirzelAlgorithm(
    platform=ParallelExecutionPlatforms.THREADING,
    units_number=12,  # how many threads
    key="bikeid",
)
cep = CEP([citibikeHotPathsPattern], parallel_execution_params=dp_params, storage_params=load_shedding_params )

events = CitiBikeDataFrameInputStream(
    input_file,
    timestamp_column="starttime",
)

monitor.run(
    cep.run,
    events,
    FileOutputStream("../test/demo/Matches/testing", output_file),
    CitiBikeDataFormatter(),
)

Creating evaluation manager...
 - Parallel execution: <parallel.ParallelExecutionParameters.DataParallelExecutionParametersHirzelAlgorithm object at 0x11d3bca10>
 - Storage: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.3, load_shedding_strategy=oldest,latency_bound=0.08)
 - Using ParallelExecutionModes.DATA_PARALLELISM execution mode
Tree calling create_storage_unit with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.3, load_shedding_strategy=oldest,latency_bound=0.08)
LeafNode.create_storage_unit called with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, en

Exception in thread Thread-6 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation/

we are updating event count 248000
computed currlat 1.146398
Found match: {'tripduration': '104', 'starttime': 2019-01-08 12:53:33.200000, 'stoptime': 2019-01-08 12:55:17.645000, 'startstationid': '326', 'endstationid': '236', 'bikeid': '34654', 'eventid': 246900}
{'tripduration': '356', 'starttime': 2019-01-08 12:55:20.357000, 'stoptime': 2019-01-08 13:01:17.326000, 'startstationid': '236', 'endstationid': '111111', 'bikeid': '34654', 'eventid': 246965}


event count 248087 3253.935975667
computed currlat 1.146398
Found match: {'tripduration': '73', 'starttime': 2019-01-08 13:11:45.406000, 'stoptime': 2019-01-08 13:12:58.484000, 'startstationid': '259', 'endstationid': '427', 'bikeid': '33615', 'eventid': 247450}
{'tripduration': '1290', 'starttime': 2019-01-08 13:13:02.735000, 'stoptime': 2019-01-08 13:34:33.205000, 'startstationid': '427', 'endstationid': '111111', 'bikeid': '33615', 'eventid': 247476}


event count 248647 3254.030315083
we are updating event count 249000
we are upd

Exception in thread Thread-11 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

we are updating event count 331000
we are updating event count 332000
we are updating event count 333000
computed currlat 1.146398
Found match: {'tripduration': '136', 'starttime': 2019-01-10 15:53:22.812000, 'stoptime': 2019-01-10 15:55:39.106000, 'startstationid': '311', 'endstationid': '307', 'bikeid': '27846', 'eventid': 338750}
{'tripduration': '472', 'starttime': 2019-01-10 15:55:40.358000, 'stoptime': 2019-01-10 16:03:32.716000, 'startstationid': '307', 'endstationid': '111111', 'bikeid': '27846', 'eventid': 338832}


event count 333197 3266.767096708
computed currlat 1.146398
Found match: {'tripduration': '109', 'starttime': 2019-01-10 16:20:46.677000, 'stoptime': 2019-01-10 16:22:36.621000, 'startstationid': '128', 'endstationid': '3467', 'bikeid': '16381', 'eventid': 339700}
{'tripduration': '1176', 'starttime': 2019-01-10 16:22:37.199000, 'stoptime': 2019-01-10 16:42:13.589000, 'startstationid': '3467', 'endstationid': '111111', 'bikeid': '16381', 'eventid': 339758}


event 

...

Exception in thread Thread-12 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

we are updating event count 635000
we are updating event count 636000
we are updating event count 637000
computed currlat 1.146398
Found match: {'tripduration': '500', 'starttime': 2019-01-27 06:37:30.921000, 'stoptime': 2019-01-27 06:45:51.005000, 'startstationid': '350', 'endstationid': '3701', 'bikeid': '33149', 'eventid': 828100}
{'tripduration': '299', 'starttime': 2019-01-27 06:45:55.295000, 'stoptime': 2019-01-27 06:50:54.854000, 'startstationid': '3701', 'endstationid': '111111', 'bikeid': '33149', 'eventid': 828121}


event count 637607 3315.038489958
we are updating event count 638000
computed currlat 1.146398
Found match: {'tripduration': '173', 'starttime': 2019-01-26 19:43:21.583000, 'stoptime': 2019-01-26 19:46:15.474000, 'startstationid': '412', 'endstationid': '531', 'bikeid': '19578', 'eventid': 823800}
{'tripduration': '564', 'starttime': 2019-01-26 19:46:15.628000, 'stoptime': 2019-01-26 19:55:40.306000, 'startstationid': '531', 'endstationid': '111111', 'bikeid': '1

Exception in thread Thread-9 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation/

we are updating event count 668000
computed currlat 1.146398
Found match: {'tripduration': '169', 'starttime': 2019-01-28 12:44:57.703000, 'stoptime': 2019-01-28 12:47:47.344000, 'startstationid': '3454', 'endstationid': '3081', 'bikeid': '35387', 'eventid': 871600}
{'tripduration': '702', 'starttime': 2019-01-28 12:47:48.190000, 'stoptime': 2019-01-28 12:59:30.981000, 'startstationid': '3081', 'endstationid': '111111', 'bikeid': '35387', 'eventid': 871661}


event count 668897 3320.153655333
we are updating event count 669000
computed currlat 1.146398
Found match: {'tripduration': '70', 'starttime': 2019-01-28 21:32:19.283000, 'stoptime': 2019-01-28 21:33:29.990000, 'startstationid': '3576', 'endstationid': '3574', 'bikeid': '32077', 'eventid': 891150}
{'tripduration': '1696', 'starttime': 2019-01-28 21:33:31.329000, 'stoptime': 2019-01-28 22:01:47.890000, 'startstationid': '3574', 'endstationid': '111111', 'bikeid': '32077', 'eventid': 891180}


event count 669900 3320.320157417
we a

144.151411

# VARIANT 2
#### RECENT_LATENCIES_INTERVAL = 1000

In [4]:
# VARIANT 2
input_file = "../test/EventFiles/201901-citibike-tripdata-1-fabricated-original.csv"
output_file = "output_citibike_VARIANT_2.txt"

citibikeHotPathsPattern = get_pattern(timedelta_minutes=31)
load_shedding_threshold = 30  # when to start load shedding - length of partial match array
load_shedding_drop_rate = 0.15  # how many matches to drop when load shedding is active
latency_bound = 0.08  # in seconds


load_shedding_params = TreeStorageParameters(
    sort_storage=True,
    enable_load_shedding=True,
    load_shedding_threshold=load_shedding_threshold,
    load_shedding_drop_rate=load_shedding_drop_rate,
    load_shedding_strategy="oldest",
    clean_up_interval=10,
    latency_bound=latency_bound,
)
dp_params = DataParallelExecutionParametersHirzelAlgorithm(
    platform=ParallelExecutionPlatforms.THREADING,
    units_number=12,  # how many threads
    key="bikeid",
)
cep = CEP([citibikeHotPathsPattern], parallel_execution_params=dp_params, storage_params=load_shedding_params )

events = CitiBikeDataFrameInputStream(
    input_file,
    timestamp_column="starttime",
)

monitor.run(
    cep.run,
    events,
    FileOutputStream("../test/demo/Matches/testing", output_file),
    CitiBikeDataFormatter(),
)

Creating evaluation manager...
 - Parallel execution: <parallel.ParallelExecutionParameters.DataParallelExecutionParametersHirzelAlgorithm object at 0x11d3ff5f0>
 - Storage: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.15, load_shedding_strategy=oldest,latency_bound=0.08)
 - Using ParallelExecutionModes.DATA_PARALLELISM execution mode
Tree calling create_storage_unit with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.15, load_shedding_strategy=oldest,latency_bound=0.08)
LeafNode.create_storage_unit called with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, 

Exception in thread Thread-18 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

computed currlat 1.64341
Found match: {'tripduration': '104', 'starttime': 2019-01-08 12:53:33.200000, 'stoptime': 2019-01-08 12:55:17.645000, 'startstationid': '326', 'endstationid': '236', 'bikeid': '34654', 'eventid': 246900}
{'tripduration': '356', 'starttime': 2019-01-08 12:55:20.357000, 'stoptime': 2019-01-08 13:01:17.326000, 'startstationid': '236', 'endstationid': '111111', 'bikeid': '34654', 'eventid': 246965}


event count 951410 3581.781696625
we are updating event count 952000
computed currlat 1.64341
Found match: {'tripduration': '73', 'starttime': 2019-01-08 13:11:45.406000, 'stoptime': 2019-01-08 13:12:58.484000, 'startstationid': '259', 'endstationid': '427', 'bikeid': '33615', 'eventid': 247450}
{'tripduration': '1290', 'starttime': 2019-01-08 13:13:02.735000, 'stoptime': 2019-01-08 13:34:33.205000, 'startstationid': '427', 'endstationid': '111111', 'bikeid': '33615', 'eventid': 247476}


event count 952110 3582.170906125
computed currlat 1.64341
Found match: {'tripdur

Exception in thread Thread-23 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

we are updating event count 1035000
computed currlat 1.64341
Found match: {'tripduration': '100', 'starttime': 2019-01-10 14:03:10.939000, 'stoptime': 2019-01-10 14:04:51.932000, 'startstationid': '3285', 'endstationid': '3289', 'bikeid': '35115', 'eventid': 335550}
{'tripduration': '506', 'starttime': 2019-01-10 14:04:52.526000, 'stoptime': 2019-01-10 14:13:18.647000, 'startstationid': '3289', 'endstationid': '111111', 'bikeid': '35115', 'eventid': 335605}


event count 1035004 3626.382601625
computed currlat 1.64341
Found match: {'tripduration': '152', 'starttime': 2019-01-10 13:18:43.882000, 'stoptime': 2019-01-10 13:21:16.782000, 'startstationid': '3431', 'endstationid': '517', 'bikeid': '35111', 'eventid': 334350}
{'tripduration': '475', 'starttime': 2019-01-10 13:21:17.431000, 'stoptime': 2019-01-10 13:29:12.840000, 'startstationid': '517', 'endstationid': '111111', 'bikeid': '35111', 'eventid': 334422}


event count 1035671 3626.745359667
we are updating event count 1036000
comp

...

Exception in thread Thread-24 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

we are updating event count 1340000
computed currlat 3.852161
Found match: {'tripduration': '191', 'starttime': 2019-01-26 19:09:51.183000, 'stoptime': 2019-01-26 19:13:02.364000, 'startstationid': '465', 'endstationid': '529', 'bikeid': '35741', 'eventid': 823050}
{'tripduration': '452', 'starttime': 2019-01-26 19:13:06.155000, 'stoptime': 2019-01-26 19:20:38.540000, 'startstationid': '529', 'endstationid': '111111', 'bikeid': '35741', 'eventid': 823138}


event count 1340319 3963.775594417
we are updating event count 1341000
computed currlat 3.852161
Found match: {'tripduration': '196', 'starttime': 2019-01-26 20:25:25.131000, 'stoptime': 2019-01-26 20:28:41.485000, 'startstationid': '3016', 'endstationid': '3109', 'bikeid': '24797', 'eventid': 824600}
{'tripduration': '1010', 'starttime': 2019-01-26 20:28:43.609000, 'stoptime': 2019-01-26 20:45:34.539000, 'startstationid': '3109', 'endstationid': '111111', 'bikeid': '24797', 'eventid': 824665}


event count 1341087 3964.191777292
co

Exception in thread Thread-21 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

computed currlat 3.852161
Found match: {'tripduration': '104', 'starttime': 2019-01-29 11:09:57.041000, 'stoptime': 2019-01-29 11:11:41.523000, 'startstationid': '3002', 'endstationid': '363', 'bikeid': '25674', 'eventid': 906950}
{'tripduration': '604', 'starttime': 2019-01-29 11:11:46.544000, 'stoptime': 2019-01-29 11:21:50.554000, 'startstationid': '363', 'endstationid': '111111', 'bikeid': '25674', 'eventid': 906985}


event count 1373550 3981.773987
computed currlat 3.852161
Found match: {'tripduration': '216', 'starttime': 2019-01-28 12:21:47.953000, 'stoptime': 2019-01-28 12:25:24.421000, 'startstationid': '426', 'endstationid': '82', 'bikeid': '28235', 'eventid': 871043}
{'tripduration': '303', 'starttime': 2019-01-28 12:25:25.376000, 'stoptime': 2019-01-28 12:30:28.727000, 'startstationid': '82', 'endstationid': '111111', 'bikeid': '28235', 'eventid': 871128}


event count 1373661 3981.8338105
computed currlat 3.852161
Found match: {'tripduration': '169', 'starttime': 2019-01-

586.000221

# VARIANT 3
#### RECENT_LATENCIES_INTERVAL = 1000

In [3]:
# VARIANT 3
input_file = "../test/EventFiles/201901-citibike-tripdata-1-fabricated-original.csv"
output_file = "output_citibike_VARIANT_3.txt"

citibikeHotPathsPattern = get_pattern(timedelta_minutes=31)
load_shedding_threshold = 30  # when to start load shedding - length of partial match array
load_shedding_drop_rate = 0.1  # how many matches to drop when load shedding is active
latency_bound = 0.08  # in seconds


load_shedding_params = TreeStorageParameters(
    sort_storage=True,
    enable_load_shedding=True,
    load_shedding_threshold=load_shedding_threshold,
    load_shedding_drop_rate=load_shedding_drop_rate,
    load_shedding_strategy="oldest",
    clean_up_interval=10,
    latency_bound=latency_bound,
)
dp_params = DataParallelExecutionParametersHirzelAlgorithm(
    platform=ParallelExecutionPlatforms.THREADING,
    units_number=12,  # how many threads
    key="bikeid",
)
cep = CEP([citibikeHotPathsPattern], parallel_execution_params=dp_params, storage_params=load_shedding_params )

events = CitiBikeDataFrameInputStream(
    input_file,
    timestamp_column="starttime",
)

monitor.run(
    cep.run,
    events,
    FileOutputStream("../test/demo/Matches/testing", output_file),
    CitiBikeDataFormatter(),
)

Creating evaluation manager...
 - Parallel execution: <parallel.ParallelExecutionParameters.DataParallelExecutionParametersHirzelAlgorithm object at 0x11cac2360>
 - Storage: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.1, load_shedding_strategy=oldest,latency_bound=0.08)
 - Using ParallelExecutionModes.DATA_PARALLELISM execution mode
Tree calling create_storage_unit with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.1, load_shedding_strategy=oldest,latency_bound=0.08)
LeafNode.create_storage_unit called with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, en

Exception in thread Thread-6 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation/

computed currlat 1.658812
Found match: {'tripduration': '73', 'starttime': 2019-01-08 13:11:45.406000, 'stoptime': 2019-01-08 13:12:58.484000, 'startstationid': '259', 'endstationid': '427', 'bikeid': '33615', 'eventid': 247450}
{'tripduration': '1290', 'starttime': 2019-01-08 13:13:02.735000, 'stoptime': 2019-01-08 13:34:33.205000, 'startstationid': '427', 'endstationid': '111111', 'bikeid': '33615', 'eventid': 247476}


event count 248735 4829.374765792
we are updating event count 249000
we are updating event count 250000
computed currlat 1.658812
Found match: {'tripduration': '163', 'starttime': 2019-01-08 14:08:28.422000, 'stoptime': 2019-01-08 14:11:11.766000, 'startstationid': '503', 'endstationid': '3139', 'bikeid': '15603', 'eventid': 249079}
{'tripduration': '835', 'starttime': 2019-01-08 14:11:11.810000, 'stoptime': 2019-01-08 14:25:06.941000, 'startstationid': '3139', 'endstationid': '111111', 'bikeid': '15603', 'eventid': 249168}


event count 250289 4832.419707917
we are u

Exception in thread Thread-11 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

we are updating event count 332000
computed currlat 1.658812
Found match: {'tripduration': '152', 'starttime': 2019-01-10 13:18:43.882000, 'stoptime': 2019-01-10 13:21:16.782000, 'startstationid': '3431', 'endstationid': '517', 'bikeid': '35111', 'eventid': 334350}
{'tripduration': '475', 'starttime': 2019-01-10 13:21:17.431000, 'stoptime': 2019-01-10 13:29:12.840000, 'startstationid': '517', 'endstationid': '111111', 'bikeid': '35111', 'eventid': 334422}


event count 332566 4993.668414875
computed currlat 1.658812
Found match: {'tripduration': '182', 'starttime': 2019-01-10 14:53:11.421000, 'stoptime': 2019-01-10 14:56:13.913000, 'startstationid': '3463', 'endstationid': '285', 'bikeid': '34414', 'eventid': 336950}
{'tripduration': '468', 'starttime': 2019-01-10 14:56:20.370000, 'stoptime': 2019-01-10 15:04:09.293000, 'startstationid': '285', 'endstationid': '111111', 'bikeid': '34414', 'eventid': 337029}


event count 332861 4994.251707958
we are updating event count 333000
computed

...

Exception in thread Thread-12 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

we are updating event count 635000
computed currlat 0.081324
Found match: {'tripduration': '191', 'starttime': 2019-01-26 19:09:51.183000, 'stoptime': 2019-01-26 19:13:02.364000, 'startstationid': '465', 'endstationid': '529', 'bikeid': '35741', 'eventid': 823050}
{'tripduration': '452', 'starttime': 2019-01-26 19:13:06.155000, 'stoptime': 2019-01-26 19:20:38.540000, 'startstationid': '529', 'endstationid': '111111', 'bikeid': '35741', 'eventid': 823138}


event count 635196 5596.128708083
computed currlat 0.081324
Found match: {'tripduration': '106', 'starttime': 2019-01-26 11:51:12.837000, 'stoptime': 2019-01-26 11:52:59.121000, 'startstationid': '3321', 'endstationid': '3315', 'bikeid': '33251', 'eventid': 807850}
{'tripduration': '407', 'starttime': 2019-01-26 11:52:59.756000, 'stoptime': 2019-01-26 11:59:47.256000, 'startstationid': '3315', 'endstationid': '111111', 'bikeid': '33251', 'eventid': 807935}


event count 635372 5596.479452958
computed currlat 0.081324
Found match: {'t

Exception in thread Thread-9 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation/

computed currlat 0.081324
Found match: {'tripduration': '216', 'starttime': 2019-01-28 12:21:47.953000, 'stoptime': 2019-01-28 12:25:24.421000, 'startstationid': '426', 'endstationid': '82', 'bikeid': '28235', 'eventid': 871043}
{'tripduration': '303', 'starttime': 2019-01-28 12:25:25.376000, 'stoptime': 2019-01-28 12:30:28.727000, 'startstationid': '82', 'endstationid': '111111', 'bikeid': '28235', 'eventid': 871128}


event count 668598 5662.993774167
computed currlat 0.081324
Found match: {'tripduration': '169', 'starttime': 2019-01-28 12:44:57.703000, 'stoptime': 2019-01-28 12:47:47.344000, 'startstationid': '3454', 'endstationid': '3081', 'bikeid': '35387', 'eventid': 871600}
{'tripduration': '702', 'starttime': 2019-01-28 12:47:48.190000, 'stoptime': 2019-01-28 12:59:30.981000, 'startstationid': '3081', 'endstationid': '111111', 'bikeid': '35387', 'eventid': 871661}


event count 668862 5663.545508458
we are updating event count 669000
computed currlat 0.081324
Found match: {'tri

2194.011428

# VARIANT 4
#### 1000

In [3]:
# VARIANT 4
# changed latency_bound to 0.1, rest is as variant 1
input_file = "../test/EventFiles/201901-citibike-tripdata-1-fabricated-original.csv"
output_file = "output_citibike_VARIANT_4.txt"

citibikeHotPathsPattern = get_pattern(timedelta_minutes=31)
load_shedding_threshold = 30  # when to start load shedding - length of partial match array
load_shedding_drop_rate = 0.3  # how many matches to drop when load shedding is active
latency_bound = 0.1  # in seconds


load_shedding_params = TreeStorageParameters(
    sort_storage=True,
    enable_load_shedding=True,
    load_shedding_threshold=load_shedding_threshold,
    load_shedding_drop_rate=load_shedding_drop_rate,
    load_shedding_strategy="oldest",
    clean_up_interval=10,
    latency_bound=latency_bound,
)
dp_params = DataParallelExecutionParametersHirzelAlgorithm(
    platform=ParallelExecutionPlatforms.THREADING,
    units_number=12,  # how many threads
    key="bikeid",
)
cep = CEP([citibikeHotPathsPattern], parallel_execution_params=dp_params, storage_params=load_shedding_params )

events = CitiBikeDataFrameInputStream(
    input_file,
    timestamp_column="starttime",
)

monitor.run(
    cep.run,
    events,
    FileOutputStream("../test/demo/Matches/testing", output_file),
    CitiBikeDataFormatter(),
)

Creating evaluation manager...
 - Parallel execution: <parallel.ParallelExecutionParameters.DataParallelExecutionParametersHirzelAlgorithm object at 0x11c776030>
 - Storage: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.3, load_shedding_strategy=oldest,latency_bound=0.1)
 - Using ParallelExecutionModes.DATA_PARALLELISM execution mode
Tree calling create_storage_unit with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.3, load_shedding_strategy=oldest,latency_bound=0.1)
LeafNode.create_storage_unit called with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enab

Exception in thread Thread-6 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation/

we are updating event count 248000
computed currlat 1.141339
Found match: {'tripduration': '104', 'starttime': 2019-01-08 12:53:33.200000, 'stoptime': 2019-01-08 12:55:17.645000, 'startstationid': '326', 'endstationid': '236', 'bikeid': '34654', 'eventid': 246900}
{'tripduration': '356', 'starttime': 2019-01-08 12:55:20.357000, 'stoptime': 2019-01-08 13:01:17.326000, 'startstationid': '236', 'endstationid': '111111', 'bikeid': '34654', 'eventid': 246965}


event count 248163 6743.578874583
computed currlat 1.141339
Found match: {'tripduration': '73', 'starttime': 2019-01-08 13:11:45.406000, 'stoptime': 2019-01-08 13:12:58.484000, 'startstationid': '259', 'endstationid': '427', 'bikeid': '33615', 'eventid': 247450}
{'tripduration': '1290', 'starttime': 2019-01-08 13:13:02.735000, 'stoptime': 2019-01-08 13:34:33.205000, 'startstationid': '427', 'endstationid': '111111', 'bikeid': '33615', 'eventid': 247476}


event count 248695 6743.664898667
we are updating event count 249000
we are upd

Exception in thread Thread-11 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

we are updating event count 331000
we are updating event count 332000
we are updating event count 333000
computed currlat 1.141339
Found match: {'tripduration': '136', 'starttime': 2019-01-10 15:53:22.812000, 'stoptime': 2019-01-10 15:55:39.106000, 'startstationid': '311', 'endstationid': '307', 'bikeid': '27846', 'eventid': 338750}
{'tripduration': '472', 'starttime': 2019-01-10 15:55:40.358000, 'stoptime': 2019-01-10 16:03:32.716000, 'startstationid': '307', 'endstationid': '111111', 'bikeid': '27846', 'eventid': 338832}


event count 333169 6756.357277583
computed currlat 1.141339
Found match: {'tripduration': '109', 'starttime': 2019-01-10 16:20:46.677000, 'stoptime': 2019-01-10 16:22:36.621000, 'startstationid': '128', 'endstationid': '3467', 'bikeid': '16381', 'eventid': 339700}
{'tripduration': '1176', 'starttime': 2019-01-10 16:22:37.199000, 'stoptime': 2019-01-10 16:42:13.589000, 'startstationid': '3467', 'endstationid': '111111', 'bikeid': '16381', 'eventid': 339758}


event 

...

Exception in thread Thread-12 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

we are updating event count 635000
computed currlat 1.141339
Found match: {'tripduration': '196', 'starttime': 2019-01-26 20:25:25.131000, 'stoptime': 2019-01-26 20:28:41.485000, 'startstationid': '3016', 'endstationid': '3109', 'bikeid': '24797', 'eventid': 824600}
{'tripduration': '1010', 'starttime': 2019-01-26 20:28:43.609000, 'stoptime': 2019-01-26 20:45:34.539000, 'startstationid': '3109', 'endstationid': '111111', 'bikeid': '24797', 'eventid': 824665}


event count 635793 6804.439114125
computed currlat 1.141339
Found match: {'tripduration': '192', 'starttime': 2019-01-26 20:34:27.656000, 'stoptime': 2019-01-26 20:37:39.900000, 'startstationid': '437', 'endstationid': '3047', 'bikeid': '19709', 'eventid': 824750}
{'tripduration': '324', 'starttime': 2019-01-26 20:37:55.377000, 'stoptime': 2019-01-26 20:43:19.986000, 'startstationid': '3047', 'endstationid': '111111', 'bikeid': '19709', 'eventid': 824803}


event count 635858 6804.450168042
computed currlat 1.141339
Found match: 

Exception in thread Thread-9 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation/

we are updating event count 668000
computed currlat 1.141339
Found match: {'tripduration': '169', 'starttime': 2019-01-28 12:44:57.703000, 'stoptime': 2019-01-28 12:47:47.344000, 'startstationid': '3454', 'endstationid': '3081', 'bikeid': '35387', 'eventid': 871600}
{'tripduration': '702', 'starttime': 2019-01-28 12:47:48.190000, 'stoptime': 2019-01-28 12:59:30.981000, 'startstationid': '3081', 'endstationid': '111111', 'bikeid': '35387', 'eventid': 871661}


event count 668939 6809.947483292
we are updating event count 669000
computed currlat 1.141339
Found match: {'tripduration': '70', 'starttime': 2019-01-28 21:32:19.283000, 'stoptime': 2019-01-28 21:33:29.990000, 'startstationid': '3576', 'endstationid': '3574', 'bikeid': '32077', 'eventid': 891150}
{'tripduration': '1696', 'starttime': 2019-01-28 21:33:31.329000, 'stoptime': 2019-01-28 22:01:47.890000, 'startstationid': '3574', 'endstationid': '111111', 'bikeid': '32077', 'eventid': 891180}


event count 669882 6810.105213875
we a

144.082933

# VARIANT 5

In [3]:
# VARIANT 5
# changed latency_bound to 0.1, rest is as variant 2
input_file = "../test/EventFiles/201901-citibike-tripdata-1-fabricated-original.csv"
output_file = "output_citibike_VARIANT_5.txt"

citibikeHotPathsPattern = get_pattern(timedelta_minutes=31)
load_shedding_threshold = 30  # when to start load shedding - length of partial match array
load_shedding_drop_rate = 0.15  # how many matches to drop when load shedding is active
latency_bound = 0.1  # in seconds


load_shedding_params = TreeStorageParameters(
    sort_storage=True,
    enable_load_shedding=True,
    load_shedding_threshold=load_shedding_threshold,
    load_shedding_drop_rate=load_shedding_drop_rate,
    load_shedding_strategy="oldest",
    clean_up_interval=10,
    latency_bound=latency_bound,
)
dp_params = DataParallelExecutionParametersHirzelAlgorithm(
    platform=ParallelExecutionPlatforms.THREADING,
    units_number=12,  # how many threads
    key="bikeid",
)
cep = CEP([citibikeHotPathsPattern], parallel_execution_params=dp_params, storage_params=load_shedding_params )

events = CitiBikeDataFrameInputStream(
    input_file,
    timestamp_column="starttime",
)

monitor.run(
    cep.run,
    events,
    FileOutputStream("../test/demo/Matches/testing", output_file),
    CitiBikeDataFormatter(),
)

Creating evaluation manager...
 - Parallel execution: <parallel.ParallelExecutionParameters.DataParallelExecutionParametersHirzelAlgorithm object at 0x11cd97350>
 - Storage: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.15, load_shedding_strategy=oldest,latency_bound=0.1)
 - Using ParallelExecutionModes.DATA_PARALLELISM execution mode
Tree calling create_storage_unit with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.15, load_shedding_strategy=oldest,latency_bound=0.1)
LeafNode.create_storage_unit called with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, en

Exception in thread Thread-6 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation/

computed currlat 1.391591
Found match: {'tripduration': '104', 'starttime': 2019-01-08 12:53:33.200000, 'stoptime': 2019-01-08 12:55:17.645000, 'startstationid': '326', 'endstationid': '236', 'bikeid': '34654', 'eventid': 246900}
{'tripduration': '356', 'starttime': 2019-01-08 12:55:20.357000, 'stoptime': 2019-01-08 13:01:17.326000, 'startstationid': '236', 'endstationid': '111111', 'bikeid': '34654', 'eventid': 246965}


event count 247956 7191.980192708
we are updating event count 248000
computed currlat 1.391591
Found match: {'tripduration': '73', 'starttime': 2019-01-08 13:11:45.406000, 'stoptime': 2019-01-08 13:12:58.484000, 'startstationid': '259', 'endstationid': '427', 'bikeid': '33615', 'eventid': 247450}
{'tripduration': '1290', 'starttime': 2019-01-08 13:13:02.735000, 'stoptime': 2019-01-08 13:34:33.205000, 'startstationid': '427', 'endstationid': '111111', 'bikeid': '33615', 'eventid': 247476}


event count 248581 7192.343886208
we are updating event count 249000
we are upd

Exception in thread Thread-11 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

we are updating event count 332000
computed currlat 1.391591
Found match: {'tripduration': '152', 'starttime': 2019-01-10 13:18:43.882000, 'stoptime': 2019-01-10 13:21:16.782000, 'startstationid': '3431', 'endstationid': '517', 'bikeid': '35111', 'eventid': 334350}
{'tripduration': '475', 'starttime': 2019-01-10 13:21:17.431000, 'stoptime': 2019-01-10 13:29:12.840000, 'startstationid': '517', 'endstationid': '111111', 'bikeid': '35111', 'eventid': 334422}


event count 332528 7239.835000292
computed currlat 1.391591
Found match: {'tripduration': '182', 'starttime': 2019-01-10 14:53:11.421000, 'stoptime': 2019-01-10 14:56:13.913000, 'startstationid': '3463', 'endstationid': '285', 'bikeid': '34414', 'eventid': 336950}
{'tripduration': '468', 'starttime': 2019-01-10 14:56:20.370000, 'stoptime': 2019-01-10 15:04:09.293000, 'startstationid': '285', 'endstationid': '111111', 'bikeid': '34414', 'eventid': 337029}


event count 332813 7239.992458083
we are updating event count 333000
computed

...

Exception in thread Thread-12 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

computed currlat 0.177687
Found match: {'tripduration': '244', 'starttime': 2019-01-27 02:22:55.218000, 'stoptime': 2019-01-27 02:26:59.795000, 'startstationid': '3373', 'endstationid': '3419', 'bikeid': '27909', 'eventid': 827750}
{'tripduration': '567', 'starttime': 2019-01-27 02:28:14.533000, 'stoptime': 2019-01-27 02:37:41.776000, 'startstationid': '3419', 'endstationid': '111111', 'bikeid': '27909', 'eventid': 827758}


event count 637541 7616.558717792
computed currlat 0.177687
Found match: {'tripduration': '744', 'starttime': 2019-01-27 02:37:58.760000, 'stoptime': 2019-01-27 02:50:22.878000, 'startstationid': '111111', 'endstationid': '3687', 'bikeid': '27909', 'eventid': 827775}
{'tripduration': '350', 'starttime': 2019-01-27 02:50:39.130000, 'stoptime': 2019-01-27 02:56:29.177000, 'startstationid': '3687', 'endstationid': '111111', 'bikeid': '27909', 'eventid': 827805}


event count 637596 7616.591497917
computed currlat 0.177687
Found match: {'tripduration': '1171', 'startti

Exception in thread Thread-9 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation/

we are updating event count 649000
computed currlat 0.177687
Found match: {'tripduration': '592', 'starttime': 2019-01-27 01:20:49.159000, 'stoptime': 2019-01-27 01:30:41.886000, 'startstationid': '311', 'endstationid': '3298', 'bikeid': '28283', 'eventid': 827484}
{'tripduration': '446', 'starttime': 2019-01-27 01:30:50.487000, 'stoptime': 2019-01-27 01:38:17.269000, 'startstationid': '3298', 'endstationid': '111111', 'bikeid': '28283', 'eventid': 827546}


event count 649622 7623.636664708
computed currlat 0.177687
computed currlat 0.177687
Found match: {'tripduration': '514', 'starttime': 2019-01-27 01:22:54.336000, 'stoptime': 2019-01-27 01:31:28.521000, 'startstationid': '362', 'endstationid': '482', 'bikeid': '26699', 'eventid': 827500}
{'tripduration': '322', 'starttime': 2019-01-27 01:32:22.630000, 'stoptime': 2019-01-27 01:37:45.056000, 'startstationid': '482', 'endstationid': '3094', 'bikeid': '26699', 'eventid': 827552}
{'tripduration': '460', 'starttime': 2019-01-27 01:37:5

638.076257

# VARIANT 6

In [3]:
# VARIANT 6
input_file = "../test/EventFiles/201901-citibike-tripdata-1-fabricated-original.csv"
output_file = "output_citibike_VARIANT_6.txt"

citibikeHotPathsPattern = get_pattern(timedelta_minutes=31)
load_shedding_threshold = 30  # when to start load shedding - length of partial match array
load_shedding_drop_rate = 0.1  # how many matches to drop when load shedding is active
latency_bound = 0.1  # in seconds


load_shedding_params = TreeStorageParameters(
    sort_storage=True,
    enable_load_shedding=True,
    load_shedding_threshold=load_shedding_threshold,
    load_shedding_drop_rate=load_shedding_drop_rate,
    load_shedding_strategy="oldest",
    clean_up_interval=10,
    latency_bound=latency_bound,
)
dp_params = DataParallelExecutionParametersHirzelAlgorithm(
    platform=ParallelExecutionPlatforms.THREADING,
    units_number=12,  # how many threads
    key="bikeid",
)
cep = CEP([citibikeHotPathsPattern], parallel_execution_params=dp_params, storage_params=load_shedding_params )

events = CitiBikeDataFrameInputStream(
    input_file,
    timestamp_column="starttime",
)

monitor.run(
    cep.run,
    events,
    FileOutputStream("../test/demo/Matches/testing", output_file),
    CitiBikeDataFormatter(),
)

Creating evaluation manager...
 - Parallel execution: <parallel.ParallelExecutionParameters.DataParallelExecutionParametersHirzelAlgorithm object at 0x11d775b50>
 - Storage: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.1, load_shedding_strategy=oldest,latency_bound=0.1)
 - Using ParallelExecutionModes.DATA_PARALLELISM execution mode
Tree calling create_storage_unit with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.1, load_shedding_strategy=oldest,latency_bound=0.1)
LeafNode.create_storage_unit called with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enab

Exception in thread Thread-6 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation/

computed currlat 1767.285028
Found match: {'tripduration': '73', 'starttime': 2019-01-08 13:11:45.406000, 'stoptime': 2019-01-08 13:12:58.484000, 'startstationid': '259', 'endstationid': '427', 'bikeid': '33615', 'eventid': 247450}
{'tripduration': '1290', 'starttime': 2019-01-08 13:13:02.735000, 'stoptime': 2019-01-08 13:34:33.205000, 'startstationid': '427', 'endstationid': '111111', 'bikeid': '33615', 'eventid': 247476}


event count 248788 9239.395089666
we are updating event count 249000
computed currlat 1767.285028
Found match: {'tripduration': '166', 'starttime': 2019-01-08 12:36:46.278000, 'stoptime': 2019-01-08 12:39:32.973000, 'startstationid': '3435', 'endstationid': '251', 'bikeid': '15679', 'eventid': 246400}
{'tripduration': '451', 'starttime': 2019-01-08 12:39:34.591000, 'stoptime': 2019-01-08 12:47:05.674000, 'startstationid': '251', 'endstationid': '111111', 'bikeid': '15679', 'eventid': 246494}


event count 249878 9241.575525041
we are updating event count 250000
com

Exception in thread Thread-11 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

computed currlat 1767.285028
Found match: {'tripduration': '152', 'starttime': 2019-01-10 13:18:43.882000, 'stoptime': 2019-01-10 13:21:16.782000, 'startstationid': '3431', 'endstationid': '517', 'bikeid': '35111', 'eventid': 334350}
{'tripduration': '475', 'starttime': 2019-01-10 13:21:17.431000, 'stoptime': 2019-01-10 13:29:12.840000, 'startstationid': '517', 'endstationid': '111111', 'bikeid': '35111', 'eventid': 334422}


event count 332631 9409.003111125
computed currlat 1767.285028
Found match: {'tripduration': '182', 'starttime': 2019-01-10 14:53:11.421000, 'stoptime': 2019-01-10 14:56:13.913000, 'startstationid': '3463', 'endstationid': '285', 'bikeid': '34414', 'eventid': 336950}
{'tripduration': '468', 'starttime': 2019-01-10 14:56:20.370000, 'stoptime': 2019-01-10 15:04:09.293000, 'startstationid': '285', 'endstationid': '111111', 'bikeid': '34414', 'eventid': 337029}


event count 332792 9409.363125
we are updating event count 333000
computed currlat 1767.285028
Found match

...

Exception in thread Thread-12 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

we are updating event count 635000
computed currlat 0.678435
Found match: {'tripduration': '191', 'starttime': 2019-01-26 19:09:51.183000, 'stoptime': 2019-01-26 19:13:02.364000, 'startstationid': '465', 'endstationid': '529', 'bikeid': '35741', 'eventid': 823050}
{'tripduration': '452', 'starttime': 2019-01-26 19:13:06.155000, 'stoptime': 2019-01-26 19:20:38.540000, 'startstationid': '529', 'endstationid': '111111', 'bikeid': '35741', 'eventid': 823138}


event count 635176 10024.609802541
computed currlat 0.678435
Found match: {'tripduration': '106', 'starttime': 2019-01-26 11:51:12.837000, 'stoptime': 2019-01-26 11:52:59.121000, 'startstationid': '3321', 'endstationid': '3315', 'bikeid': '33251', 'eventid': 807850}
{'tripduration': '407', 'starttime': 2019-01-26 11:52:59.756000, 'stoptime': 2019-01-26 11:59:47.256000, 'startstationid': '3315', 'endstationid': '111111', 'bikeid': '33251', 'eventid': 807935}


event count 635425 10025.106239875
computed currlat 0.678435
Found match: {

Exception in thread Thread-9 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation/

computed currlat 0.678435
Found match: {'tripduration': '216', 'starttime': 2019-01-28 12:21:47.953000, 'stoptime': 2019-01-28 12:25:24.421000, 'startstationid': '426', 'endstationid': '82', 'bikeid': '28235', 'eventid': 871043}
{'tripduration': '303', 'starttime': 2019-01-28 12:25:25.376000, 'stoptime': 2019-01-28 12:30:28.727000, 'startstationid': '82', 'endstationid': '111111', 'bikeid': '28235', 'eventid': 871128}


event count 668668 10092.865872458
computed currlat 0.678435
Found match: {'tripduration': '169', 'starttime': 2019-01-28 12:44:57.703000, 'stoptime': 2019-01-28 12:47:47.344000, 'startstationid': '3454', 'endstationid': '3081', 'bikeid': '35387', 'eventid': 871600}
{'tripduration': '702', 'starttime': 2019-01-28 12:47:48.190000, 'stoptime': 2019-01-28 12:59:30.981000, 'startstationid': '3081', 'endstationid': '111111', 'bikeid': '35387', 'eventid': 871661}


event count 668924 10093.388648375
we are updating event count 669000
computed currlat 0.678435
Found match: {'t

4715.481199

# VARIANT 1 - random shedding

In [3]:
# VARIANT 1 - random
input_file = "../test/EventFiles/201901-citibike-tripdata-1-fabricated-original.csv"
output_file = "output_citibike_VARIANT_1_RANDOM.txt"

citibikeHotPathsPattern = get_pattern(timedelta_minutes=31)
load_shedding_threshold = 30  # when to start load shedding - length of partial match array
load_shedding_drop_rate = 0.3  # how many matches to drop when load shedding is active
latency_bound = 0.08  # in seconds


load_shedding_params = TreeStorageParameters(
    sort_storage=True,
    enable_load_shedding=True,
    load_shedding_threshold=load_shedding_threshold,
    load_shedding_drop_rate=load_shedding_drop_rate,
    load_shedding_strategy="random",
    clean_up_interval=10,
    latency_bound=latency_bound,
)
dp_params = DataParallelExecutionParametersHirzelAlgorithm(
    platform=ParallelExecutionPlatforms.THREADING,
    units_number=12,  # how many threads
    key="bikeid",
)
cep = CEP([citibikeHotPathsPattern], parallel_execution_params=dp_params, storage_params=load_shedding_params )

events = CitiBikeDataFrameInputStream(
    input_file,
    timestamp_column="starttime",
)

monitor.run(
    cep.run,
    events,
    FileOutputStream("../test/demo/Matches/testing", output_file),
    CitiBikeDataFormatter(),
)

Creating evaluation manager...
 - Parallel execution: <parallel.ParallelExecutionParameters.DataParallelExecutionParametersHirzelAlgorithm object at 0x10f7624e0>
 - Storage: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.3, load_shedding_strategy=random,latency_bound=0.08)
 - Using ParallelExecutionModes.DATA_PARALLELISM execution mode
Tree calling create_storage_unit with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.3, load_shedding_strategy=random,latency_bound=0.08)
LeafNode.create_storage_unit called with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, en

Exception in thread Thread-6 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation/

we are updating event count 248000
we are updating event count 249000
we are updating event count 250000
we are updating event count 251000
we are updating event count 252000
we are updating event count 253000
we are updating event count 254000
we are updating event count 255000
we are updating event count 256000
we are updating event count 257000
we are updating event count 258000
we are updating event count 259000
we are updating event count 260000
we are updating event count 261000
computed currlat 1.047717
Found match: {'tripduration': '107', 'starttime': 2019-01-09 00:18:04.620000, 'stoptime': 2019-01-09 00:19:51.749000, 'startstationid': '3660', 'endstationid': '285', 'bikeid': '27020', 'eventid': 271917}
{'tripduration': '2742', 'starttime': 2019-01-09 00:20:01.561000, 'stoptime': 2019-01-09 01:05:43.813000, 'startstationid': '285', 'endstationid': '111111', 'bikeid': '27020', 'eventid': 271922}


event count 261916 12649.028520292
we are updating event count 262000
computed cur

Exception in thread Thread-11 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

we are updating event count 332000
we are updating event count 333000
we are updating event count 334000
we are updating event count 335000
we are updating event count 336000
we are updating event count 337000
we are updating event count 338000
computed currlat 1.047717
Found match: {'tripduration': '274', 'starttime': 2019-01-10 21:30:12.163000, 'stoptime': 2019-01-10 21:34:46.229000, 'startstationid': '491', 'endstationid': '476', 'bikeid': '33549', 'eventid': 353550}
{'tripduration': '603', 'starttime': 2019-01-10 21:34:57.826000, 'stoptime': 2019-01-10 21:45:00.879000, 'startstationid': '476', 'endstationid': '111111', 'bikeid': '33549', 'eventid': 353631}


event count 338952 12660.16127825
we are updating event count 339000
we are updating event count 340000
we are updating event count 341000
computed currlat 1.047717
Found match: {'tripduration': '302', 'starttime': 2019-01-11 11:03:17.790000, 'stoptime': 2019-01-11 11:08:20.668000, 'startstationid': '509', 'endstationid': '482'

...

Exception in thread Thread-12 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

we are updating event count 635000
computed currlat 1.047717
Found match: {'tripduration': '192', 'starttime': 2019-01-26 20:34:27.656000, 'stoptime': 2019-01-26 20:37:39.900000, 'startstationid': '437', 'endstationid': '3047', 'bikeid': '19709', 'eventid': 824750}
{'tripduration': '324', 'starttime': 2019-01-26 20:37:55.377000, 'stoptime': 2019-01-26 20:43:19.986000, 'startstationid': '3047', 'endstationid': '111111', 'bikeid': '19709', 'eventid': 824803}


event count 635788 12704.133051
we are updating event count 636000
computed currlat 1.047717
Found match: {'tripduration': '278', 'starttime': 2019-01-26 22:24:35.608000, 'stoptime': 2019-01-26 22:29:14.457000, 'startstationid': '533', 'endstationid': '3072', 'bikeid': '28577', 'eventid': 826115}
{'tripduration': '859', 'starttime': 2019-01-26 22:29:38.120000, 'stoptime': 2019-01-26 22:43:57.316000, 'startstationid': '3072', 'endstationid': '111111', 'bikeid': '28577', 'eventid': 826159}


event count 636514 12704.243611334
we are 

Exception in thread Thread-9 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation/

we are updating event count 669000
computed currlat 1.047717
Found match: {'tripduration': '227', 'starttime': 2019-01-28 14:30:08.501000, 'stoptime': 2019-01-28 14:33:56.491000, 'startstationid': '258', 'endstationid': '324', 'bikeid': '35039', 'eventid': 874250}
{'tripduration': '2451', 'starttime': 2019-01-28 14:34:02.470000, 'stoptime': 2019-01-28 15:14:53.753000, 'startstationid': '324', 'endstationid': '111111', 'bikeid': '35039', 'eventid': 874336}


event count 669930 12709.257956292
we are updating event count 670000
computed currlat 1.047717
Found match: {'tripduration': '229', 'starttime': 2019-01-29 05:38:20.267000, 'stoptime': 2019-01-29 05:42:10.109000, 'startstationid': '417', 'endstationid': '3664', 'bikeid': '30013', 'eventid': 893150}
{'tripduration': '1626', 'starttime': 2019-01-29 05:42:22.503000, 'stoptime': 2019-01-29 06:09:28.973000, 'startstationid': '3664', 'endstationid': '111111', 'bikeid': '30013', 'eventid': 893182}


event count 670592 12709.358369334
we a

137.289898

#V3 RANDOM

In [3]:
# VARIANT 3
input_file = "../test/EventFiles/201901-citibike-tripdata-1-fabricated-original.csv"
output_file = "output_citibike_VARIANT_3_RANDOM.txt"

citibikeHotPathsPattern = get_pattern(timedelta_minutes=31)
load_shedding_threshold = 30  # when to start load shedding - length of partial match array
load_shedding_drop_rate = 0.1  # how many matches to drop when load shedding is active
latency_bound = 0.08  # in seconds


load_shedding_params = TreeStorageParameters(
    sort_storage=True,
    enable_load_shedding=True,
    load_shedding_threshold=load_shedding_threshold,
    load_shedding_drop_rate=load_shedding_drop_rate,
    load_shedding_strategy="random",
    clean_up_interval=10,
    latency_bound=latency_bound,
)
dp_params = DataParallelExecutionParametersHirzelAlgorithm(
    platform=ParallelExecutionPlatforms.THREADING,
    units_number=12,  # how many threads
    key="bikeid",
)
cep = CEP([citibikeHotPathsPattern], parallel_execution_params=dp_params, storage_params=load_shedding_params )

events = CitiBikeDataFrameInputStream(
    input_file,
    timestamp_column="starttime",
)

monitor.run(
    cep.run,
    events,
    FileOutputStream("../test/demo/Matches/testing", output_file),
    CitiBikeDataFormatter(),
)

Creating evaluation manager...
 - Parallel execution: <parallel.ParallelExecutionParameters.DataParallelExecutionParametersHirzelAlgorithm object at 0x11a186360>
 - Storage: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.1, load_shedding_strategy=random,latency_bound=0.08)
 - Using ParallelExecutionModes.DATA_PARALLELISM execution mode
Tree calling create_storage_unit with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, enable_load_shedding=True, load_shedding_threshold=30, load_shedding_drop_rate=0.1, load_shedding_strategy=random,latency_bound=0.08)
LeafNode.create_storage_unit called with storage_params: TreeStorageParameters(sort_storage=True, attributes_priorities={}, clean_up_interval=10, prioritize_sorting_by_timestamp=True, en

Exception in thread Thread-6 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation/

we are updating event count 248000
computed currlat 1.06634
Found match: {'tripduration': '250', 'starttime': 2019-01-08 12:48:22.778000, 'stoptime': 2019-01-08 12:52:33.439000, 'startstationid': '461', 'endstationid': '326', 'bikeid': '34654', 'eventid': 246751}
{'tripduration': '104', 'starttime': 2019-01-08 12:53:33.200000, 'stoptime': 2019-01-08 12:55:17.645000, 'startstationid': '326', 'endstationid': '236', 'bikeid': '34654', 'eventid': 246900}
{'tripduration': '356', 'starttime': 2019-01-08 12:55:20.357000, 'stoptime': 2019-01-08 13:01:17.326000, 'startstationid': '236', 'endstationid': '111111', 'bikeid': '34654', 'eventid': 246965}


event count 248022 13598.840123125
computed currlat 1.06634
Found match: {'tripduration': '73', 'starttime': 2019-01-08 13:11:45.406000, 'stoptime': 2019-01-08 13:12:58.484000, 'startstationid': '259', 'endstationid': '427', 'bikeid': '33615', 'eventid': 247450}
{'tripduration': '1290', 'starttime': 2019-01-08 13:13:02.735000, 'stoptime': 2019-01-

Exception in thread Thread-11 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

computed currlat 1.06634
Found match: {'tripduration': '152', 'starttime': 2019-01-10 13:18:43.882000, 'stoptime': 2019-01-10 13:21:16.782000, 'startstationid': '3431', 'endstationid': '517', 'bikeid': '35111', 'eventid': 334350}
{'tripduration': '475', 'starttime': 2019-01-10 13:21:17.431000, 'stoptime': 2019-01-10 13:29:12.840000, 'startstationid': '517', 'endstationid': '111111', 'bikeid': '35111', 'eventid': 334422}


event count 332665 13759.900338792
we are updating event count 333000
computed currlat 1.06634
Found match: {'tripduration': '136', 'starttime': 2019-01-10 15:53:22.812000, 'stoptime': 2019-01-10 15:55:39.106000, 'startstationid': '311', 'endstationid': '307', 'bikeid': '27846', 'eventid': 338750}
{'tripduration': '472', 'starttime': 2019-01-10 15:55:40.358000, 'stoptime': 2019-01-10 16:03:32.716000, 'startstationid': '307', 'endstationid': '111111', 'bikeid': '27846', 'eventid': 338832}


event count 333183 13760.903129667
we are updating event count 334000
computed 

...

Exception in thread Thread-12 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation

we are updating event count 635000
computed currlat 0.097148
Found match: {'tripduration': '130', 'starttime': 2019-01-27 11:05:58.078000, 'stoptime': 2019-01-27 11:08:08.870000, 'startstationid': '3338', 'endstationid': '3351', 'bikeid': '34377', 'eventid': 832650}
{'tripduration': '755', 'starttime': 2019-01-27 11:08:10.025000, 'stoptime': 2019-01-27 11:20:45.542000, 'startstationid': '3351', 'endstationid': '111111', 'bikeid': '34377', 'eventid': 832726}


event count 635622 14337.22959625
computed currlat 0.097148
Found match: {'tripduration': '196', 'starttime': 2019-01-26 20:25:25.131000, 'stoptime': 2019-01-26 20:28:41.485000, 'startstationid': '3016', 'endstationid': '3109', 'bikeid': '24797', 'eventid': 824600}
{'tripduration': '1010', 'starttime': 2019-01-26 20:28:43.609000, 'stoptime': 2019-01-26 20:45:34.539000, 'startstationid': '3109', 'endstationid': '111111', 'bikeid': '24797', 'eventid': 824665}


event count 635915 14337.816213167
we are updating event count 636000
co

Exception in thread Thread-9 (_run):
Traceback (most recent call last):
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1073, in _bootstrap_inner
    self.run()
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/venv/lib/python3.12/site-packages/ipykernel/ipkernel.py", line 772, in run_closure
    _threading_Thread_run(self)
  File "/opt/miniconda3/lib/python3.12/threading.py", line 1010, in run
    self._target(*self._args, **self._kwargs)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/data_parallel/DataParallelExecutionAlgorithm.py", line 119, in _run
    evaluation_manager.eval(events, matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/parallel/manager/SequentialEvaluationManager.py", line 32, in eval
    self.__eval_mechanism.eval(event_stream, pattern_matches, data_formatter)
  File "/Users/cricoche/Desktop/aalto_master/SSDM/OpenCEP recover/OpenCEP/tree/evaluation/

computed currlat 0.096145
Found match: {'tripduration': '216', 'starttime': 2019-01-28 12:21:47.953000, 'stoptime': 2019-01-28 12:25:24.421000, 'startstationid': '426', 'endstationid': '82', 'bikeid': '28235', 'eventid': 871043}
{'tripduration': '303', 'starttime': 2019-01-28 12:25:25.376000, 'stoptime': 2019-01-28 12:30:28.727000, 'startstationid': '82', 'endstationid': '111111', 'bikeid': '28235', 'eventid': 871128}


event count 668769 14401.247832083
we are updating event count 669000
computed currlat 0.096145
Found match: {'tripduration': '169', 'starttime': 2019-01-28 12:44:57.703000, 'stoptime': 2019-01-28 12:47:47.344000, 'startstationid': '3454', 'endstationid': '3081', 'bikeid': '35387', 'eventid': 871600}
{'tripduration': '702', 'starttime': 2019-01-28 12:47:48.190000, 'stoptime': 2019-01-28 12:59:30.981000, 'startstationid': '3081', 'endstationid': '111111', 'bikeid': '35387', 'eventid': 871661}


event count 669017 14401.718831417
computed currlat 0.096145
computed currlat

3061.816723